In [44]:
import logging
from datetime import datetime, timezone
from typing import List

from redis.asyncio import Redis

from app.database_redis.connection import get_redis_client
from app.database_redis.dals.connection_dal import ConnectionDAL
from app.services.apis.streamqueue_service.client import StreamQueueServiceAPI
from app.services.apis.streamqueue_service.schemas import AudioChunkInfo, ExistingConnectionInfo
from app.services.audio.redis import Connection, Diarizer, Meeting, Transcriber
from app.settings import settings

logger = logging.getLogger(__name__)


In [45]:
from app.services.audio.audio import AudioFileCorruptedError, AudioSlicer

In [46]:
import pandas as pd

In [94]:
redis_client = await get_redis_client(settings.redis_host, settings.redis_port, settings.redis_password)

In [95]:
connection_id = 'test'

In [96]:
path = f'/audio/{connection_id}.webm'

In [97]:
audio_slicer = await AudioSlicer.from_ffmpeg_slice(path, 0, 300)
slice_duration = audio_slicer.audio.duration_seconds
audio_data = await audio_slicer.export_data()

2024-06-22 19:38:38,986 - INFO - app.services.audio.audio - start: None


In [98]:
audio_slicer.audio

In [99]:
meeting_id = 'test5'
user_id = 'ac43a16f-2a2c-41d7-99f7-035e4893c64f'

In [100]:
n = 25

In [105]:

segment_start_timestamp = pd.Timestamp.utcnow()+ pd.Timedelta(seconds = n)
segment_end_timestamp = segment_start_timestamp + pd.Timedelta(seconds = n)
current_time = datetime.now(timezone.utc)
connection = Connection(redis_client, connection_id, user_id)
await connection.update_timestamps(segment_start_timestamp, segment_end_timestamp)
meeting = Meeting(redis_client, meeting_id)

await meeting.load_from_redis()
await meeting.add_connection(connection.id)
await meeting.set_start_timestamp(segment_start_timestamp)
meeting.diarizer_last_updated_timestamp = meeting.diarizer_last_updated_timestamp or segment_start_timestamp
meeting.transcriber_last_updated_timestamp = (
    meeting.transcriber_last_updated_timestamp or segment_start_timestamp
)

print("diarizer added")
diarizer = Diarizer(redis_client)
await diarizer.add_todo(meeting.meeting_id)
await meeting.update_diarizer_timestamp(
    segment_start_timestamp, diarizer_last_updated_timestamp=current_time+ pd.Timedelta(seconds = n)
)

print("transcriber added")
transcriber = Transcriber(redis_client)
await transcriber.add_todo(meeting.meeting_id)
await meeting.update_transcriber_timestamp(
    segment_start_timestamp, transcriber_last_updated_timestamp=current_time+ pd.Timedelta(seconds = n)
)

print(segment_start_timestamp)
n+=25

diarizer added
transcriber added
2024-06-22 19:41:39.972002+00:00


In [ ]:
await meeting.update_redis()